In [1]:
import pandas as pd
import numpy as np
from scipy import stats, integrate
import seaborn as sns
import matplotlib.pyplot as plt
from copy import deepcopy
plt.rcParams['font.sans-serif'] = ['SimHei']
plt.rcParams['axes.unicode_minus'] = False
from matplotlib.font_manager import FontProperties
myfont = FontProperties(fname = "C:\Windows\Fonts\simhei.ttf", size = 14)
sns.set(font = myfont.get_name())
import nltk
from nltk.tokenize import sent_tokenize, word_tokenize

from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all" # 一个cell显示多输出
pd.set_option('display.max_rows', 100) # 设置最大显示100行
pd.set_option('display.max_columns', 100) # 设置最大显示100列


In [2]:
cleanedDataPcf = pd.read_csv("CleanedData/pacifier.csv", index_col = 0, parse_dates=['review_date'])

encodedDataPcf = deepcopy(cleanedDataPcf)

cleanedDataMcw = pd.read_csv("CleanedData/microwave.csv", index_col = 0, parse_dates=['review_date'])

encodedDataMcw = deepcopy(cleanedDataMcw)

cleanedDataHdr = pd.read_csv("CleanedData/hair_dryer.csv", index_col = 0, parse_dates=['review_date'])

encodedDataHdr = deepcopy(cleanedDataHdr)

In [3]:
encodedDataPcf = encodedDataPcf[["customer_id", "review_id", 
                                 "product_id", "star_rating", 
                                 "helpful_votes", "total_votes", 
                                 "vine", "verified_purchase", 
                                 "review_headline", "review_body", 
                                "review_date"]]

encodedDataMcw = encodedDataMcw[["customer_id", "review_id", 
                                 "product_id", "star_rating", 
                                 "helpful_votes", "total_votes", 
                                 "vine", "verified_purchase", 
                                 "review_headline", "review_body", 
                                "review_date"]]

encodedDataHdr = encodedDataHdr[["customer_id", "review_id", 
                                 "product_id", "star_rating", 
                                 "helpful_votes", "total_votes", 
                                 "vine", "verified_purchase", 
                                 "review_headline", "review_body", 
                                "review_date"]]

只提取有意义的特征

In [4]:
encodedDataPcf["vine"] = (encodedDataPcf["vine"] == 'Y') | (encodedDataPcf["vine"] == 'y')

encodedDataMcw["vine"] = (encodedDataMcw["vine"] == 'Y') | (encodedDataMcw["vine"] == 'y')

encodedDataHdr["vine"] = (encodedDataHdr["vine"] == 'Y') | (encodedDataHdr["vine"] == 'y')

encodedDataPcf["verified_purchase"] = (encodedDataPcf["verified_purchase"] == 'Y') | (encodedDataPcf["verified_purchase"] == 'y')

encodedDataMcw["verified_purchase"] = (encodedDataMcw["verified_purchase"] == 'Y') | (encodedDataMcw["verified_purchase"] == 'y')

encodedDataHdr["verified_purchase"] = (encodedDataHdr["verified_purchase"] == 'Y') | (encodedDataHdr["verified_purchase"] == 'y')

把逻辑特征转为布尔值

In [5]:
encodedDataPcf["product_id"] = encodedDataPcf["product_id"].str.upper()

encodedDataMcw["product_id"] = encodedDataMcw["product_id"].str.upper()

encodedDataHdr["product_id"] = encodedDataHdr["product_id"].str.upper()

encodedDataPcf["customer_id"] = encodedDataPcf["customer_id"].astype("str")

encodedDataMcw["customer_id"] = encodedDataMcw["customer_id"].astype("str")

encodedDataHdr["customer_id"] = encodedDataHdr["customer_id"].astype("str")

encodedDataPcf["review_id"] = encodedDataPcf["review_id"].str.upper()

encodedDataMcw["review_id"] = encodedDataMcw["review_id"].str.upper()

encodedDataHdr["review_id"] = encodedDataHdr["review_id"].str.upper()

处理Unique Id

In [6]:
customerDataBase = {
    
}
"""
helpfulnessRatio [helpful, total]
isVine [bool]
purchasedRatio [purchased, total]
"""

for id in encodedDataPcf["customer_id"] :
    
    if(id not in customerDataBase) : customerDataBase[id] = {"helpfulnessRatio" : [1, 2], "isVine" : False, "purchasedRatio" : [0, 0]}
    
for id in encodedDataMcw["customer_id"] :
    
    if(id not in customerDataBase) : customerDataBase[id] = {"helpfulnessRatio" : [1, 2], "isVine" : False, "purchasedRatio" : [0, 0]}
    
for id in encodedDataHdr["customer_id"] :
    
    if(id not in customerDataBase) : customerDataBase[id] = {"helpfulnessRatio" : [1, 2], "isVine" : False, "purchasedRatio" : [0, 0]}

        
for i in range(0, len(encodedDataPcf)) :
    
    row = encodedDataPcf.iloc[i]
    
    customerDataBase[row["customer_id"]]["helpfulnessRatio"][0] += row["helpful_votes"]
    
    customerDataBase[row["customer_id"]]["helpfulnessRatio"][1] += row["total_votes"]
    
    customerDataBase[row["customer_id"]]["isVine"] |= row["vine"]
    
    customerDataBase[row["customer_id"]]["purchasedRatio"][0] += row["verified_purchase"]
    
    customerDataBase[row["customer_id"]]["purchasedRatio"][1] += 1
    
for i in range(0, len(encodedDataMcw)) :
    
    row = encodedDataMcw.iloc[i]
    
    customerDataBase[row["customer_id"]]["helpfulnessRatio"][0] += row["helpful_votes"]
    
    customerDataBase[row["customer_id"]]["helpfulnessRatio"][1] += row["total_votes"]
    
    customerDataBase[row["customer_id"]]["isVine"] |= row["vine"]
    
    customerDataBase[row["customer_id"]]["purchasedRatio"][0] += row["verified_purchase"]
    
    customerDataBase[row["customer_id"]]["purchasedRatio"][1] += 1
    

for i in range(0, len(encodedDataHdr)) :
    
    row = encodedDataHdr.iloc[i]
    
    customerDataBase[row["customer_id"]]["helpfulnessRatio"][0] += row["helpful_votes"]
    
    customerDataBase[row["customer_id"]]["helpfulnessRatio"][1] += row["total_votes"]
    
    customerDataBase[row["customer_id"]]["isVine"] |= row["vine"]
    
    customerDataBase[row["customer_id"]]["purchasedRatio"][0] += row["verified_purchase"]
    
    customerDataBase[row["customer_id"]]["purchasedRatio"][1] += 1
    

生成评论者数据库，注意有用性投票经过了拉普拉斯平滑

In [7]:
customerDataBase

{'40626522': {'helpfulnessRatio': [1, 2],
  'isVine': False,
  'purchasedRatio': [1, 1]},
 '16290022': {'helpfulnessRatio': [1, 2],
  'isVine': False,
  'purchasedRatio': [1, 1]},
 '10216509': {'helpfulnessRatio': [1, 2],
  'isVine': False,
  'purchasedRatio': [1, 1]},
 '114040': {'helpfulnessRatio': [1, 2],
  'isVine': False,
  'purchasedRatio': [2, 2]},
 '27971579': {'helpfulnessRatio': [1, 2],
  'isVine': False,
  'purchasedRatio': [1, 1]},
 '36369192': {'helpfulnessRatio': [1, 2],
  'isVine': False,
  'purchasedRatio': [1, 1]},
 '18742061': {'helpfulnessRatio': [1, 2],
  'isVine': False,
  'purchasedRatio': [1, 1]},
 '15312194': {'helpfulnessRatio': [1, 2],
  'isVine': False,
  'purchasedRatio': [1, 1]},
 '44791277': {'helpfulnessRatio': [1, 2],
  'isVine': False,
  'purchasedRatio': [1, 1]},
 '2943530': {'helpfulnessRatio': [1, 2],
  'isVine': False,
  'purchasedRatio': [1, 1]},
 '32717440': {'helpfulnessRatio': [1, 2],
  'isVine': False,
  'purchasedRatio': [1, 1]},
 '2761934': {

In [8]:
productDataBasePcf = {
    
}
productDataBaseMcw = {
    
}
productDataBaseHdr = {
    
}
"""
reviews
"""

for id in encodedDataPcf["product_id"] :
    
    if(id not in productDataBasePcf) : productDataBasePcf[id] = []
    
for id in encodedDataMcw["product_id"] :
    
    if(id not in productDataBaseMcw) : productDataBaseMcw[id] = []
        
for id in encodedDataHdr["product_id"] :
    
    if(id not in productDataBaseHdr) : productDataBaseHdr[id] = []
    
        
for i in range(0, len(encodedDataPcf)) :
    
    row = encodedDataPcf.iloc[i]
    
    productDataBasePcf[row["product_id"]].append(row)
    
for i in range(0, len(encodedDataMcw)) :
    
    row = encodedDataMcw.iloc[i]
    
    productDataBaseMcw[row["product_id"]].append(row)

for i in range(0, len(encodedDataHdr)) :
    
    row = encodedDataHdr.iloc[i]
    
    productDataBaseHdr[row["product_id"]].append(row)


In [10]:
encodedProductDataBasePcf = {
    
}
encodedProductDataBaseMcw = {
    
}
encodedProductDataBaseHdr = {
    
}
"""
rating
truthnesss(Reputation of reviewer)
NLP score
"""

for id in productDataBasePcf :
    reviews = productDataBasePcf[id]
    
    encodedProductDataBasePcf[id] = []
    
    for i in reviews :
        
        reviewHeadline = i["review_headline"]
        
        reviewBody = str(i["review_body"])
        
        reviewBody = reviewBody.replace("<br/>", "")
        
        print(word_tokenize(reviewBody))
        
        encodedProductDataBasePcf[id].append(
        [
            int(i["star_rating"]), 
            customerDataBase[i["customer_id"]]["helpfulnessRatio"][0] / customerDataBase[i["customer_id"]]["helpfulnessRatio"][1], 
            0, 
            i["review_date"]
        ])

['Perfect', 'match', 'for', 'the', 'Gund', 'Huggybuddy', 'I', 'bought', 'as', 'a', 'baby', 'gift', '.']
['So', 'cute', '!']
['This', 'little', 'lamb', 'is', 'just', 'so', 'precious', '.', 'I', 'was', 'really', 'hoping', 'my', 'daughter', 'would', 'love', 'her', 'Wubbanub', 'as', 'much', 'as', 'I', 'have', 'seen', 'so', 'many', 'other', 'baby', 'have', ',', 'but', 'sadly', ',', 'nope', ':', '(', 'but', 'that', 'is', "n't", 'the', 'companies', 'fault', '.', 'These', 'are', 'just', 'fantastic', '.', 'If', 'I', 'had', 'to', 'criticize', 'one', 'thing', 'it', 'would', 'be', 'that', 'they', 'are', 'rather', 'hard', 'to', 'sanitize', '.', 'I', 'had', 'been', 'wiping', 'it', 'down', 'with', 'pacifier', 'wipes', 'but', 'I', 'like', 'to', 'boil', 'and', 'microwave', 'sanitize', 'my', 'pacifiers', 'and', 'you', 'are', 'not', 'able', 'to', 'do', 'that', 'with', 'this', '.', 'I', 'tried', 'holding', 'just', 'the', 'pacifier', 'in', 'boiling', 'water', 'but', 'the', 'steam', 'got', 'too', 'hot', 'an

['Easy', 'for', 'the', 'little', 'ones', 'to', 'hold', '.', 'Our', 'little', 'one', 'loves', 'it', '.']
['The', 'stuffie', 'is', 'wonderfully', 'made', 'And', 'my', 'sweet', 'girl', 'looks', 'adorable', 'with', 'it', 'and', 'genuinely', 'seems', 'to', 'like', 'it', '!', 'I', 'recommend', 'it', 'and', 'am', 'ordering', 'a', 'second', 'these', 'rock', '!', '!', '!', ':', ')', 'Very', 'happy', 'momma', '!']
['My', 'newborn', "'s", 'best', 'friend', '!', 'I', 'tried', 'giving', 'her', 'another', 'pacifier', 'that', 'had', 'a', 'slant', 'nipple', 'but', 'she', 'did', "n't", 'like', 'it', 'at', 'all', '.', 'She', 'likes', 'this', 'style', 'nipple', 'way', 'better', '.', 'It', "'s", 'great', 'having', 'the', 'stuffed', 'animal', 'on', 'the', 'pacifier', 'because', 'I', 'can', 'always', 'see', 'where', 'it', 'is', '.', 'I', 'did', "n't", 'realize', 'you', 'could', "n't", 'separate', 'the', 'two', '.', 'I', 'normally', 'like', 'to', 'sterilize', 'bottles/nipples/pacifiers', 'at', 'least', 'once

['My', 'daughter', 'was', 'having', 'a', 'hard', 'time', 'keeping', 'her', 'paci', 'in', ',', 'and', 'every', 'time', 'we', 'put', 'her', 'to', 'bed', 'it', 'would', 'pop', 'out', 'and', 'she', 'would', 'start', 'fussing', 'until', 'we', 'came', 'and', 'put', 'it', 'back', 'in', '.', 'I', 'wanted', 'something', 'to', 'prop', 'it', 'in', 'there', 'with', 'but', 'did', "n't", 'want', 'to', 'have', 'a', 'suffication', 'hazard', 'so', 'I', 'found', 'the', 'Wubbanub', '!', '&', 'it', 'worked', 'like', 'magic', '!', 'We', 'set', 'it', 'on', 'her', 'chest', 'or', 'on', 'the', 'bed', 'next', 'to', 'her', 'and', 'it', 'keeps', 'her', 'paci', 'in', 'until', 'she', 'does', "n't", 'want', 'it', '.', 'Also', 'she', 'Loves', 'to', 'hold', 'on', 'to', 'the', 'soft', 'giraffe-', 'it', "'s", 'like', 'a', 'double', 'soothe', '.', 'It', 'was', 'smaller', 'than', 'I', 'thought', 'which', 'I', 'was', 'happy', 'about', '.', 'I', 'did', "n't", 'want', 'anything', 'to', 'overwhelming', 'for', 'her', '.', '(',

['So', 'cute', 'easy', 'for', 'baby', 'to', 'grab', '&', 'find', 'on', 'his', 'own']
['My', 'babies', 'favorite', 'wubbanub', '!', '!']
['We', 'have', 'the', 'dino', 'version', 'of', 'this', 'and', 'my', 'son', 'loves', 'it', 'so', 'we', 'thought', 'we', "'d", 'get', 'one', 'more', 'of', 'a', 'different', 'style', '.', 'These', 'are', 'good', 'because', 'it', "'s", 'a', 'pacifier', 'and', 'a', 'plush', 'all', 'in', 'one', '.', 'During', 'the', 'night', 'if', 'he', 'wakes', 'up', 'its', 'easy', 'for', 'him', 'to', 'find', 'in', 'the', 'dark', 'and', 'grab', 'onto', 'to', 'put', 'back', 'in', 'his', 'mouth', 'and', 'go', 'right', 'back', 'to', 'sleep', '.', 'Worth', 'it', "'s", 'weight', 'in', 'gold', 'to', 'a', 'sleep', 'deprived', 'parent', '!', '<', 'br', '/', '>', 'Note', ':', 'It', "'s", 'Machine', 'washable', ',', 'air', 'dry', '.']
['These', 'things', 'are', 'awesome', '!', 'My', 'LO', 'loves', 'his', 'WubbaNubs', '!']
['My', 'daughter', 'loves', 'her', 'Wubba', '!', '!', '!', 'It

['UPDATE', '#', '#', '#', '#', '#', 'I', 'am', 'changing', 'my', 'review', 'to', 'Neutral', '(', '3/5', ')', 'because', 'I', 'now', 'realize', 'that', 'my', '(', 'now', ')', '6', 'month', 'old', 'does', 'not', 'like', 'pacifiers', '.', 'He', 'may', 'have', 'never', 'liked', 'pacifiers', 'and', 'he', 'may', 'never', 'will', '.', 'My', '3', 'year', 'old', 'will', 'not', 'ween', 'off', 'his', 'pacifier', 'but', 'my', 'youngest', 'does', 'not', 'do', 'them', '.', 'Your', 'child', 'may', 'not', 'like', 'this', 'product', ',', 'and', 'judging', 'by', 'the', 'other', 'reviews', ',', 'it', 'may', 'not', 'be', 'the', 'Plush', 'Toy', 'Pacifier', ',', 'it', 'just', 'might', 'be', 'your', 'kid.', '<', 'br', '/', '>', '<', 'br', '/', '>', 'Let', 'me', 'just', 'say', 'that', 'this', 'is', 'the', 'worse', 'pacifier', 'ever', '.', 'If', 'I', 'could', 'use', 'profanity', 'to', 'describe', 'this', 'frustrating', 'little', 'plush', 'toy', 'pacifier', ',', 'this', 'review', 'would', 'be', 'nothing', 'but'

...

['My', 'daughter', 'loves', 'pacifiers', 'but', 'not', 'for', 'sucking', ',', 'for', 'teething', '!', 'These', 'pacis', 'are', 'really', 'easy', 'to', 'keep', 'hold', 'of', 'and', 'super', 'soft', 'on', 'swollen', 'gums', '.', 'They', 'are', 'a', 'little', 'pricey', 'though', ',', 'so', 'just', 'do', "n't", 'let', 'your', 'dog', 'see', 'them', '!']
['These', 'are', 'the', 'best', 'pacifiers', 'I', "'ve", 'ever', 'purchased', '!', 'It', 'has', 'a', 'great', ',', 'solid', 'base', '(', 'for', 'when', 'my', 'daughter', 'is', 'teething', ')', 'and', 'orthodontic', 'nipple', 'for', 'soothing/naptime', '.', 'I', 'love', 'that', 'there', 'is', 'nowhere', 'for', 'air', 'or', 'saliva', 'to', 'get', 'trapped', ',', 'making', 'these', 'one', 'of', 'the', 'most', 'sanitary', 'pacifiers', 'you', 'can', 'have', '!', 'They', 'are', 'definitely', 'more', 'expensive', 'that', 'the', 'kind', 'you', "'ll", 'find', 'in', 'Target', ',', 'but', 'I', 'think', 'they', "'re", 'worth', 'every', 'penny', '.']
['T

['My', 'toddler', 'will', 'only', 'take', 'the', 'Binky', 'that', 'is', 'pictured', '.', 'The', 'ones', 'I', 'received', 'are', 'ANGLED', 'Binkys', 'and', 'she', 'refuses', 'to', 'take', 'them', '.', 'I', 'thought', 'maybe', 'I', 'ordered', 'the', 'angled', 'ones', 'in', 'error', 'because', 'I', 'was', 'so', 'excited', 'about', 'the', 'price', '(', 'the', 'ones', 'pictured', 'are', 'selling', 'for', 'MUCH', 'HIGHER', 'because', 'Playtex', 'has', 'discontinued', 'them', ')', 'but', 'upon', 'looking', 'at', 'the', 'advertised', 'photo', 'once', 'again', ',', 'I', 'see', 'that', 'it', 'was', "n't", 'my', 'error', '.', 'It', 'was', 'a', 'major', 'disappointment', 'to', 'receive', 'the', 'wrong', 'Binkys', '.', 'I', 'could', 'purchase', 'the', 'angled', 'ones', 'anywhere', ',', 'for', 'less', 'than', 'what', 'I', 'paid', 'for', 'these', '.', 'Nonetheless', ',', 'it', 'was', 'a', 'waste', 'of', 'money', 'because', 'they', 'are', 'just', 'sitting', 'in', 'a', 'container', 'with', 'the', 'rest

['Have', "n't", 'been', 'able', 'to', 'use', 'these', 'yet', 'because', 'the', 'little', 'one', 'wo', "n't", 'be', 'here', 'till', 'February', '!', 'But', 'I', 'know', 'they', 'are', 'great', 'products', 'and', 'will', 'get', 'much', 'use', '!']
['These', 'are', 'great', 'for', 'every', 'little', 'Bulldogs', 'fan', 'out', 'there', '!', 'I', 'definitely', 'recommend', 'them', '!', 'Love', 'these', '!', 'They', 'are', 'so', 'cute', '!']
['1']
['these', 'came', 'quick', 'and', 'were', 'in', 'new', 'and', 'undamaged', 'condition', '.', 'they', 'are', 'small', 'enough', 'for', 'my', 'newborn', 'and', 'look', 'great', '!']
['Sturdy', 'and', 'colorful', '.', 'Stays', 'where', 'you', 'put', 'it', '.', 'Baby', 'loves', 'looking', 'at', 'it', 'as', 'well', '.']
['Sturdy', ',', 'easy', 'to', 'use', ',', 'my', 'kids', 'each', 'have', 'had', '&', '#', '34', ';', 'their', '&', '#', '34', ';', 'paci', 'chain', 'that', 'we', 'keep', 'long', 'after', 'the', 'paci', 'departs', '.']
['My', 'son', 'has', 

['Its', 'cute', 'its', 'adorable', 'and', 'would', 'recommend', 'it', 'for', 'any', 'one', 'with', 'infants..', ':', ')', 'I', 'bought', 'it', 'for', 'my', 'daughter', 'because', 'she', 'wanted', 'it', 'for', 'my', 'preemie', 'grandson..', 'It', 'is', 'a', 'huge', 'hit', 'in', 'he', 'NICU']
['Wubbanubs', 'are', 'the', 'only', 'paci', 'my', 'baby', 'will', 'take', '.', 'The', 'alligator', 'is', 'really', 'cute', 'and', 'easy', 'for', 'him', 'to', 'hold', 'onto', '.']
['Bought', 'this', 'for', 'my', 'cousin', "'s", 'baby', 'shower', '.', 'She', "'s", 'a', 'FL', 'Gators', 'fan', '.', 'I', 'learned', 'with', 'my', 'own', 'baby', ',', 'that', 'kids', 'love', 'these', '!']
['My', 'grandson', 'loves', 'the', 'wubbanubs', 'that', 'he', 'has', 'and', 'I', 'am', 'sure', 'he', 'will', 'love', 'this', 'one', 'that', 'I', 'will', 'put', 'in', 'his', 'Easter', 'basket']
['This', 'is', 'so', 'adorable', '.', 'My', 'husband', 'is', 'a', 'huge', 'FL', 'Gators', 'fan', 'and', 'this', 'was', 'just', 'per

['Love', 'these', 'for', 'newborns', '.', 'They', 'are', 'the', 'perfect', 'size', 'and', 'they', 'have', 'a', 'better', 'shape', 'than', 'the', 'hospital', 'provided', 'soothie', 'paci', "'s", '.']
['Hands', 'down', 'THE', 'ONLY', 'pacifier', 'that', 'has', 'worked', '!', '(', 'We', 'have', '3', 'kids', '!', ')', 'Do', "n't", 'try', 'all', 'the', 'other', 'brands', 'first', '!', 'Get', 'this', 'one', '!', 'I', 'love', 'the', 'contour', 'compared', 'to', 'the', 'big', 'hospital', 'soothies', 'and', 'it', "'s", 'soo', 'cute', '!', 'Should', 'we', 'decide', 'to', 'add', 'to', 'our', 'family', ',', 'this', 'one', 'will', 'be', 'the', 'one', 'we', 'do', '.', 'These', 'would', 'make', 'great', 'baby', 'shower', 'gift', 'stuffers', 'too', '!']
['I', 'spent', '10', 'dollars', 'including', 'shipping', 'for', 'one', 'of', 'these', 'when', 'I', 'could', 'have', 'purchased', '3', 'for', '10', '!', 'Buyer', 'beware', ',', 'BabyHaven', 'is', 'aware', 'that', 'there', 'are', 'better', 'deals', 'and'

In [ ]:
encodedProductDataBasePcf

In [ ]:
def merge_review(df):
    df['review_headline'] = df['review_headline'].apply(str)
    df['review_body'] = df['review_body'].apply(str)
    df['review'] = df['review_headline'] + '. ' + df['review_body']

In [ ]:
merge_review(encodedDataPcf)

merge_review(encodedDataMcw)

merge_review(encodedDataHdr)

In [ ]:
encodedDataPcf = encodedDataPcf.drop(['review_headline', 'review_body'], axis=1)

encodedDataMcw = encodedDataMcw.drop(['review_headline', 'review_body'], axis=1)

encodedDataHdr = encodedDataHdr.drop(['review_headline', 'review_body'], axis=1)

In [ ]:
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer

def get_review_score(sentence: str) -> float:
    analyzer = SentimentIntensityAnalyzer()
    score = analyzer.polarity_scores(sentence)
    score = score['compound']

    return score

In [ ]:
encodedDataPcf['review_score'] = encodedDataPcf['review'].map(get_review_score)

encodedDataMcw['review_score'] = encodedDataMcw['review'].map(get_review_score)

encodedDataHdr['review_score'] = encodedDataHdr['review'].map(get_review_score)

In [ ]:
encodedDataPcf.head()

encodedDataMcw.head()

encodedDataHdr.head()